In [1]:
import os
from langchain import PromptTemplate
from langchain.chains import RetrievalQA
from langchain.embeddings import HuggingFaceEmbeddings
from langchain_pinecone import PineconeVectorStore
from langchain.document_loaders import PyPDFLoader, DirectoryLoader
from langchain.text_splitter import RecursiveCharacterTextSplitter
from langchain.llms import CTransformers
from pinecone import Pinecone, ServerlessSpec

e:\maniconda\envs\mchatbot\lib\site-packages\pinecone\data\index.py:1: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from tqdm.autonotebook import tqdm


In [2]:

PINECONE_API_KEY = "63650804-25eb-4a2b-979c-83b11d35f0e9"
PINECONE_API_ENV = "us-east-1"
PINECONE_INDEX_NAME = "medicine"

In [3]:
# Set the Pinecone API key as an environment variable
os.environ["PINECONE_API_KEY"] = PINECONE_API_KEY

In [4]:
pc = Pinecone(
    api_key=os.environ.get("PINECONE_API_KEY")
)

# Check if the index exists, and create it if it doesn't
if PINECONE_INDEX_NAME not in [index.name for index in pc.list_indexes().index_list["indexes"]]:
    pc.create_index(
        name=PINECONE_INDEX_NAME, 
        dimension=768,  # Replace with the actual dimension of your embeddings
        metric='cosine',  # Or the appropriate metric for your use case
        spec=ServerlessSpec(
            cloud='aws',
            region=PINECONE_API_ENV
        )
    )

# Extract data from the PDF

In [5]:
# Extract data from the PDF
def load_pdf(data):
    loader = DirectoryLoader(data, glob="*.pdf", loader_cls=PyPDFLoader)
    documents = loader.load()
    return documents

extracted_data = load_pdf("data/")

In [6]:
extracted_data

[Document(metadata={'source': 'data\\Essential Pediatrics Ghai 8th.pdf', 'page': 0}, page_content='Eighth \nEdition '),
 Document(metadata={'source': 'data\\Essential Pediatrics Ghai 8th.pdf', 'page': 1}, page_content='Contents \nPreface to the Eighth Edition \nPreface to the First Edition \nList of Contributors \n1.Introduction to Pediatrics\nVinod KPaul\nPediatrics as a specialty \nHealth system in India 2\nNational programs on child health 3vii \nix \nxi \n2.Normal Growth and its Disorders 7\nRamesh Agarwal, Naveen Sankhyan, Vandana Jain\nSomatic growth 11\nAssessment of physical growth 11\nDisorders of growth 35 \nAbnormalities of head size and shape 39 \n3.Development 42\nRamesh Agarwal, Vandana Jain, Naveen Sankhyan\nNormal development 42 \nBehavioral disorders 57 \nHabit disorders and tics 59 \n4.Adolescent Health and\nDevelopment\nTushar R Godbole. Vijayalakshmi Bhatia\nPhysical aspects 63\nCognitive and social development 63\nProblems faced by adolescents 65\nRole of health ca

In [7]:
# Create text chunks
def text_split(extracted_data):
    text_splitter = RecursiveCharacterTextSplitter(chunk_size=500, chunk_overlap=20)
    text_chunks = text_splitter.split_documents(extracted_data)
    return text_chunks

In [8]:
text_chunks = text_split(extracted_data)
print("Length of my chunk:", len(text_chunks))

# Download embedding model
def download_hugging_face_embeddings():
    embeddings = HuggingFaceEmbeddings(model_name="sentence-transformers/all-MiniLM-L6-v2")
    return embeddings

embeddings = download_hugging_face_embeddings()

Length of my chunk: 17064


e:\maniconda\envs\mchatbot\lib\site-packages\langchain_core\_api\deprecation.py:139: LangChainDeprecationWarning: The class `HuggingFaceEmbeddings` was deprecated in LangChain 0.2.2 and will be removed in 0.3.0. An updated version of the class exists in the langchain-huggingface package and should be used instead. To use it run `pip install -U langchain-huggingface` and import as `from langchain_huggingface import HuggingFaceEmbeddings`.
  warn_deprecated(


In [9]:
# Create PineconeVectorStore from texts
vector_store = PineconeVectorStore.from_texts(
    [chunk.page_content for chunk in text_chunks],
    embeddings,
    index_name=PINECONE_INDEX_NAME
)


In [10]:
vector_store

In [11]:
# Perform a similarity search
query = "What are Allergies"
docs = vector_store.similarity_search(query, k=3)
print("Result:", docs)


Result: [Document(page_content="GALE ENCYCLOPEDIA OF MEDICINE 2 117Allergies\nAllergic rhinitis is commonly triggered by\nexposure to household dust, animal fur,or pollen. The foreign substance thattriggers an allergic reaction is calledan allergen.\nThe presence of an allergen causes the\nbody's lymphocytes to begin producingIgE antibodies. The lymphocytes of an allergy sufferer produce an unusuallylarge amount of IgE.\nIgE molecules attach to mast\ncells, which contain histamine.HistaminePollen grains\nLymphocyte\nFIRST EXPOSURE"), Document(page_content='allergens are the following:\n• plant pollens\n• animal fur and dander\n• body parts from house mites (microscopic creatures\nfound in all houses)\n• house dust• mold spores• cigarette smoke• solvents• cleaners\nCommon food allergens include the following:\n• nuts, especially peanuts, walnuts, and brazil nuts\n• fish, mollusks, and shellfish• eggs• wheat• milk• food additives and preservatives\nThe following types of drugs commonly c

In [12]:
# Perform a similarity search
query = "What are Heart Deases"
new = vector_store.similarity_search(query, k=3)
print("Result:", new)

Result: [Document(page_content='(disordered heart beat).'), Document(page_content='Coronary sinus ASD. An unroofed coronary sinus is a rare \ncommunication between the coronary sinus and the left \natrium, which produces features similar to other types of \nASD. \nPhysiology and Findings \nThe physiology of ASD is that of a pre-tricuspid shunt. \nThe enlarged right ventricle results in a parasternal \nimpulse. The ejection systolic murmur originates from the \npulmonary valve because of the increased blood flow. An \nincreased flow through the tricuspid valve may result in'), Document(page_content='some cases, removal of a small portion of the heart (abla-\ntion), implantation of a pacemaker or a cardioverterdefibrillator, or maze surgery is needed.\nIf the heart rate cannot be quickly controlled, electri-\ncal cardioversion may be used. Cardioversion, the elec-tric shock to the chest wall, is usually performed emer-gencies. This device briefly suspends the heart’s activityand allows i

In [13]:
# Define the prompt template
prompt_template = """
Use the following pieces of information to answer the user's question.
If you don't know the answer, just say that you don't know, don't try to make up an answer.

Context: {context}
Question: {question}

Only return the helpful answer below and nothing else.
Helpful answer:
"""

In [14]:
PROMPT = PromptTemplate(template=prompt_template, input_variables=["context", "question"])
chain_type_kwargs = {"prompt": PROMPT}

In [15]:
# Initialize the language model
llm = CTransformers(model="model/llama-2-7b-chat.ggmlv3.q4_0.bin",
                  model_type="llama",
                  config={'max_new_tokens': 512, 'temperature': 0.8})

In [16]:
# Set up the RetrievalQA chain
qa = RetrievalQA.from_chain_type(
    llm=llm, 
    chain_type="stuff", 
    retriever=vector_store.as_retriever(search_kwargs={'k': 2}),
    return_source_documents=True, 
    chain_type_kwargs=chain_type_kwargs
)

In [18]:
while True:
    user_input = input("Input Prompt: ")
    if user_input.lower() in ["exit", "quit"]:
        print("Exiting the chatbot.")
        break
    result = qa.invoke({"query": user_input})
    print("Response: ", result["result"])


Response:  Diabetes mellitus is a metabolic disease caused by a deficiency of insulin, which is essential to process carbohydrates in the body.
Response:  Acne is a common skin disease characterized by pimples on the face, chest, and back. It occurs when the pores of the skin become clogged with oil, dead skin cells, and bacteria.
Exiting the chatbot.
